In [25]:
import pandas as pd
import geopandas as gpd
import folium
from folium import plugins
import fiona
import json
from keplergl import KeplerGl
from geopy.distance import geodesic


# Show all trajectories on map

In [9]:

df = pd.read_csv('DataSet/DataSet/test_fix.csv', header=None, names=['time', 'id', 'sog', 'lon', 'lat', 'cog', 'delta_time', 'delta_lat', 'delta_long'])

In [11]:
# Convert 'time' column to datetime format
df['time'] = pd.to_datetime(df['time'])

C:\Users\rezas\AppData\Local\Temp\ipykernel_14384\98624784.py:2: UserWarning: Parsing dates in %d/%m/%Y %H:%M:%S format when dayfirst=False (the default) was specified. Pass `dayfirst=True` or specify a format to silence this warning.
  df['time'] = pd.to_datetime(df['time'])


In [12]:
# convert time to string
df['time'] = df['time'].astype(str)

In [16]:

# creat a kepler.gl map in a frame
map_1 = KeplerGl(height=400, data={"data_1": df})
# make the center of the map to be the center of the data
center = [df['lat'].mean(), df['lon'].mean()]
map_1.config = {'version': 'v1', 'config': {'mapState': {'latitude': center[0], 'longitude': center[1], 'zoom': 10}}}


# show the map
# map_1.save_to_html(file_name="kepler.html")

User Guide: https://docs.kepler.gl/docs/keplergl-jupyter


# Show Prediction Results

In [59]:

# minimum distance between points to be plotted on the map
min_distance = 500

# Enable KML support which is disabled by default
fiona.drvsupport.supported_drivers['kml'] = 'rw' # enable KML support which is disabled by default
fiona.drvsupport.supported_drivers['KML'] = 'rw' # enable KML support which is disabled by default
fiona.drvsupport.supported_drivers['LIBKML'] = 'rw' # enable KML support which is disabled by default

# Load KML files using geopandas
path = './Visualization/'
kml_files = ['full_source.kml', 'source.kml', 'true.kml', 'pred_LSTM.kml']  # Add paths to KML files
gdf_list = [gpd.read_file(path + kml) for kml in kml_files]

# Convert GeoDataFrames to GeoJSON strings
gdf_json_list = [gdf.to_crs(epsg='4326').to_json() for gdf in gdf_list]

# Parse the GeoJSON strings
gdf_geojson_list = [json.loads(gdf_json) for gdf_json in gdf_json_list]

# crea a list of colors to use for the layers
colors = ['grey', 'blue', 'red', 'green']

# creat map frame
f = folium.Figure(width=700, height=500)

# Create a folium map with center location and zoom level on the map
map_obj = folium.Map(location=[gdf_geojson_list[0]['features'][0]['geometry']['coordinates'][0][1],
                               gdf_geojson_list[0]['features'][0]['geometry']['coordinates'][0][0]],
                     zoom_start=7).add_to(f)


# Create FeatureGroups for each layer
line_layer = folium.FeatureGroup(name='Lines')
point_layer = folium.FeatureGroup(name='Points')

# Add FeatureGroups to the map
line_layer.add_to(map_obj)
point_layer.add_to(map_obj)


# check if the geometry is line or point
grouplayers_lines = {}
grouplayers_points = {}
for i in range(len(gdf_list)):
    if gdf_list[i].geometry.geom_type.unique() == 'LineString':
        # add layer to line layer group
        grouplayers_lines[kml_files[i].split('.')[0]] = plugins.FeatureGroupSubGroup(line_layer, kml_files[i].split('.')[0])
        map_obj.add_child(grouplayers_lines[kml_files[i].split('.')[0]])
        # Add GeoJSON layers to the map
        # for i, gdf_geojson in enumerate(gdf_geojson_list):
        gdf_geojson = gdf_geojson_list[i]
        folium.GeoJson(
            gdf_geojson,
            name=kml_files[i].split('.')[0],
            style_function=lambda x, color=colors[i]: {
                'color': color,
                'weight': 2,
                'fillOpacity': 0.5,
            }
        ).add_to(grouplayers_lines[kml_files[i].split('.')[0]])
        
    else:
        # add layer to point layer group
        grouplayers_points[kml_files[i].split('.')[0]] = plugins.FeatureGroupSubGroup(point_layer, kml_files[i].split('.')[0])
        map_obj.add_child(grouplayers_points[kml_files[i].split('.')[0]])
        # Plot points with distance greater than ... meters from the last plotted point
        prev_point = None
        for point in gdf_list[i].geometry:
            if prev_point:
                distance = geodesic((prev_point.y, prev_point.x), (point.y, point.x)).meters
                if distance > min_distance:
                    folium.Circle(
                        location=[point.y, point.x], 
                        radius=250, 
                        color=colors[i], 
                        fill=True, 
                        fill_color=colors[i], 
                        fill_opacity=1
                        ).add_to(grouplayers_points[kml_files[i].split('.')[0]])
                    prev_point = point
            else:
                folium.Circle(
                    location=[point.y, point.x], 
                    radius=250, 
                    color=colors[i], 
                    fill=True, 
                    fill_color=colors[i], 
                    fill_opacity=1
                    ).add_to(grouplayers_points[kml_files[i].split('.')[0]])
                prev_point = point
        


# Add Layer Control
folium.LayerControl(collapsed=True).add_to(map_obj)

# Display the map
map_obj


In [55]:
gdf_list[1]

Name description timestamp begin end altitudeMode  tessellate  extrude  \
0      0        None       NaT   NaT NaT         None          -1        0   
1      1        None       NaT   NaT NaT         None          -1        0   
2      2        None       NaT   NaT NaT         None          -1        0   
3      3        None       NaT   NaT NaT         None          -1        0   
4      4        None       NaT   NaT NaT         None          -1        0   
..   ...         ...       ...   ...  ..          ...         ...      ...   
245  245        None       NaT   NaT NaT         None          -1        0   
246  246        None       NaT   NaT NaT         None          -1        0   
247  247        None       NaT   NaT NaT         None          -1        0   
248  248        None       NaT   NaT NaT         None          -1        0   
249  249        None       NaT   NaT NaT         None          -1        0   

     visibility drawOrder  icon                              geometry  
0            -1      None  None  POINT Z (121.28954 27.49812 0.00000)  
1            -1      None  None  POINT Z (121.28991 27.49857 0.00000)  
2            -1      None  None  POINT Z (121.29031 27.49907 0.00000)  
3            -1      None  None  POINT Z (121.29068 27.49956 0.00000)  
4            -1      None  None  POINT Z (121.29104 27.50004 0.00000)  
..          ...       ...   ...                                   ...  
245          -1      None  None  POINT Z (121.37780 27.61807 0.00000)  
246          -1      None  None  POINT Z (121.37817 27.61853 0.00000)  
247          -1      None  None  POINT Z (121.37851 27.61896 0.00000)  
248          -1      None  None  POINT Z (121.37891 27.61949 0.00000)  
249          -1      None  None  POINT Z (121.37925 27.61994 0.00000)  

[250 rows x 12 columns]